In [1]:
import os
import numpy as np
import networkx as nx

from scipy import signal
from scipy.fft import fft, fftfreq, fftshift
from scipy.signal import find_peaks, butter, filtfilt
from scipy.ndimage import gaussian_filter
from scipy.io import wavfile

import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [2]:
data_file = "../data/scooter_example_1.wav"
fs, data = wavfile.read(data_file)

# crop data
start_time = 80 # seconds
end_time = 150 # seconds
data = data[int(start_time*fs):int(end_time*fs)]

# data_file = "../data/12062025_example.wav"
# fs, data = wavfile.read(data_file)

/var/folders/3d/d9dsxkl92nz9mr2x53ct_fvh0000gn/T/ipykernel_6782/1548117061.py:2: WavFileWarning: Chunk (non-data) not understood, skipping it.
  fs, data = wavfile.read(data_file)


In [10]:
# Spectrogram parameters
nperseg=16384
hop=0.25
noverlap=int(nperseg * (1 - hop))
window='hann'
title='Spectrogram'
colorscale='Viridis'
crop_freq=2000

# Compute spectrogram
frequencies, times, Sxx = signal.spectrogram(data, fs=fs, window=window, nperseg=nperseg, noverlap=noverlap)

# Crop frequencies if specified
if crop_freq is not None:
    freq_mask = frequencies <= crop_freq
    frequencies = frequencies[freq_mask]
    Sxx = Sxx[freq_mask, :]

# Convert to dB scale
Sxx_db = 10 * np.log10(Sxx + 1e-10)  # Add small value to avoid log(0)
# Sxx_db = np.clip(Sxx_db, a_min=-50, a_max=50)

# Create the heatmap
fig = go.Figure(data=go.Heatmap(z=Sxx_db, x=times, y=frequencies, colorscale=colorscale, colorbar=dict(title='Power (dB)')))

# Update layout
fig.update_layout(title=title, xaxis_title='Time (s)', yaxis_title='Frequency (Hz)', width=800, height=600)
fig.show()

In [28]:
win_size = 1
# positive frame
_start = 15  # seconds
_end = _start + win_size  # seconds
_start_ix, _end_ix = np.argmin(np.abs(times - _start)), np.argmin(np.abs(times - _end))
pos_frame = Sxx_db[:, _start_ix:_end_ix]
pos_corr_scores = np.corrcoef(pos_frame)

# negative frame
_start = 5  # seconds
_end = _start + win_size  # seconds
_start_ix, _end_ix = np.argmin(np.abs(times - _start)), np.argmin(np.abs(times - _end))
neg_frame = Sxx_db[:, _start_ix:_end_ix]
neg_corr_scores = np.corrcoef(neg_frame)


# Create the heatmaps and plot side by side
fig = make_subplots(rows=1, cols=2, subplot_titles=("Positive Frame Correlation", "Negative Frame Correlation"))
fig.add_trace(go.Heatmap(x=frequencies, y=frequencies, z=pos_corr_scores, colorscale='Viridis', colorbar=dict(title='Correlation')), row=1, col=1)
fig.add_trace(go.Heatmap(z=neg_corr_scores, colorscale='Viridis', colorbar=dict(title='Correlation')), row=1, col=2)

# Update layout
fig.update_layout(title_text="Correlation Matrices of Spectrogram Frames", width=1000, height=500)
fig.show()

In [29]:
# plot histogram of correlation scores
fig = make_subplots(rows=1, cols=2, subplot_titles=("Positive Frame Correlation Histogram", "Negative Frame Correlation Histogram"))
fig.add_trace(go.Histogram(x=pos_corr_scores.flatten(), nbinsx=50, name='Positive Frame'), row=1, col=1)
fig.add_trace(go.Histogram(x=neg_corr_scores.flatten(), nbinsx=50, name='Negative Frame'), row=1, col=2)
# Update layout
fig.update_layout(title_text="Histogram of Correlation Scores", width=1000, height=500)
fig.show()

In [30]:
# construct a graph

def construct_graph(corr_matrix, percentile_threshold=10):
    # Threshold the correlation matrix
    threshold = np.percentile(corr_matrix, percentile_threshold)
    adj_matrix = (corr_matrix <= threshold).astype(int)
    np.fill_diagonal(adj_matrix, 0)  # Remove self-loops

    # Create a graph from the adjacency matrix
    G = nx.from_numpy_array(adj_matrix)
    return G

# Construct graphs
pos_graph = construct_graph(pos_corr_scores, percentile_threshold=90)
neg_graph = construct_graph(neg_corr_scores, percentile_threshold=90)

In [31]:
# eigen decomposition
def graph_eigen_decomposition(G):
    # Compute the Laplacian matrix
    L = nx.laplacian_matrix(G).toarray()

    # Perform eigen decomposition
    eigenvalues, eigenvectors = np.linalg.eigh(L)

    return eigenvalues, eigenvectors

In [32]:
pos_vals, pos_vecs = graph_eigen_decomposition(pos_graph)
neg_vals, neg_vecs = graph_eigen_decomposition(neg_graph)

# plot eigenvalues
fig = make_subplots(rows=1, cols=2, subplot_titles=("Positive Frame Eigenvalues", "Negative Frame Eigenvalues"))
fig.add_trace(go.Scatter(y=pos_vals, mode='markers+lines', name='Positive Frame'), row=1, col=1)
fig.add_trace(go.Scatter(y=neg_vals, mode='markers+lines', name='Negative Frame'), row=1, col=2)
# Update layout
fig.update_layout(title_text="Eigenvalues of Graph Laplacians", width=1000, height=500)
fig.show()